In [2]:
import numpy as np
import trimesh
import matplotlib.pyplot as plt

In [2]:
# Generate torus
major_radius = 1
minor_radius = 0.4
sections = 100  # Around main ring
segments = 100  # Around minor ring

torus = trimesh.creation.torus(major_radius=major_radius, minor_radius=minor_radius, major_sections=sections, minor_sections=segments)

# Print some info
print(f"Number of vertices: {len(torus.vertices)}")
print(f"Number of faces: {len(torus.faces)}")

# Quick visualization using trimesh built-in viewer
torus.show()

Number of vertices: 10000
Number of faces: 20000


In [13]:
# Create a voxel grid with adjustable pitch (smaller pitch = higher resolution)
pitch = 0.035  # Try 0.06 or 0.045 to fine-tune total vertices
cube = trimesh.creation.box(extents=(1, 1, 1))

# Fill the bounding volume with voxels
voxelized = cube.voxelized(pitch=pitch)
boxes = voxelized.as_boxes()
mesh = trimesh.Trimesh(
    vertices=boxes.vertices,
    faces=boxes.faces,
)

print(f"Voxelized cube vertex count: {len(mesh.vertices)}")
mesh.show()

Voxelized cube vertex count: 9424


In [ ]:
# Vertices: center, top, bottom, and two fans
vertices = np.array([
    [0, 0, 0],      # 0: center (non-manifold vertex)
    [-1, 1, 0],     # 1: top left
    [0, 1, 0],      # 2: top center
    [1, 1, 0],      # 3: top right
    [-1, -1, 0],    # 4: bottom left
    [0, -1, 0],     # 5: bottom center
    [1, -1, 0],     # 6: bottom right
])

# Triangles (fans above and below center vertex)
faces = np.array([
    [0, 1, 2],  # top fan
    [0, 2, 3],
    [0, 4, 5],  # bottom fan
    [0, 5, 6],
    [0, 1, 4],  # left connector
    [0, 3, 6],  # right connector
])

mesh1 = trimesh.Trimesh(vertices=vertices, faces=faces, process=False)
mesh1.show()

In [ ]:
import trimesh
import numpy as np

# Create a basic box
box = trimesh.creation.box(extents=(1, 1, 1))

# Apply subdivision to create a finer mesh
from trimesh.remesh import subdivide
subdivided_vertices, subdivided_faces = subdivide(box.vertices, box.faces)

# Create a new mesh from the subdivided components
fine_box = trimesh.Trimesh(vertices=subdivided_vertices, faces=subdivided_faces)

# If you need an even finer mesh, you can subdivide multiple times
for _ in range(2):  # Subdivide 2 more times for an even finer mesh
    subdivided_vertices, subdivided_faces = subdivide(fine_box.vertices, fine_box.faces)
    fine_box = trimesh.Trimesh(vertices=subdivided_vertices, faces=subdivided_faces)

fine_box.show()

In [2]:
# Generate a unit cube shell mesh with ~10,000 vertices
n = 41  # 6 * 41^2 ≈ 10,086 vertices total

lin = np.linspace(0, 1, n)
u, v = np.meshgrid(lin, lin)
u = u.ravel()
v = v.ravel()

vertices = []
faces = []

def add_face(offset, normal_axis, flip=False):
    start_index = len(vertices)

    if normal_axis == 0:  # x = const
        coords = np.column_stack([np.full_like(u, offset), u, v])
    elif normal_axis == 1:  # y = const
        coords = np.column_stack([u, np.full_like(u, offset), v])
    elif normal_axis == 2:  # z = const
        coords = np.column_stack([u, v, np.full_like(u, offset)])

    if flip:
        coords = coords[:, [0, 2, 1]]

    vertices.extend(coords)

    for i in range(n - 1):
        for j in range(n - 1):
            idx0 = start_index + i * n + j
            idx1 = idx0 + 1
            idx2 = idx0 + n
            idx3 = idx2 + 1
            faces.append([idx0, idx2, idx1])
            faces.append([idx1, idx2, idx3])

# Add all 6 faces
add_face(0, normal_axis=0, flip=True)
add_face(1, normal_axis=0)
add_face(0, normal_axis=1, flip=True)
add_face(1, normal_axis=1)
add_face(0, normal_axis=2, flip=True)
add_face(1, normal_axis=2)

cube_mesh = trimesh.Trimesh(vertices=np.array(vertices), faces=np.array(faces))

# Create a scene with the mesh
# scene = trimesh.Scene([cube_mesh])

# # Render the scene
# scene.show(viewer="gl", flags={"wireframe": True})

In [5]:
len(cube_mesh.faces)

19200

In [30]:
n = 4  # 100 x 100 = 10,000 vertices
x = np.linspace(0, 1, n)
y = np.linspace(0, 1, n)
grid_x, grid_y = np.meshgrid(x, y)
vertices_2d = np.column_stack([grid_x.ravel(), grid_y.ravel()])
vertices_3d = np.hstack([vertices_2d, np.zeros((len(vertices_2d), 1))])

# Apply 45-degree rotation
rotation_angle = np.pi / 4
rotation_matrix = np.array(
    [
        [np.cos(rotation_angle), -np.sin(rotation_angle), 0],
        [np.sin(rotation_angle), np.cos(rotation_angle), 0],
        [0, 0, 1],
    ]
)
vertices_3d = vertices_3d @ rotation_matrix.T

# Manually build triangle faces
faces = []
for i in range(n - 1):
    for j in range(n - 1):
        idx0 = i * n + j
        idx1 = idx0 + 1
        idx2 = idx0 + n
        idx3 = idx2 + 1
        faces.append([idx0, idx2, idx1])
        faces.append([idx1, idx2, idx3])

mesh = trimesh.Trimesh(vertices=vertices_3d, faces=np.array(faces))

In [31]:
len(mesh.faces)

18

In [32]:
len(mesh.vertices)

16

In [29]:
mesh.faces

TrackedArray([[0, 3, 1],
              [1, 3, 4],
              [1, 4, 2],
              [2, 4, 5],
              [3, 6, 4],
              [4, 6, 7],
              [4, 7, 5],
              [5, 7, 8]])

In [7]:
mesh.show(viewer="gl", flags={"wireframe": True})

: 

In [16]:
mesh = trimesh.creation.box(extents=(1, 1, 1))

In [19]:
len(mesh.vertices)

8

In [23]:
len(mesh.faces)

12

In [22]:
mesh.show()